In [1]:
import json
with open("negacio_uab_revised_version.json","r") as f:
    data = json.load(f)
data

[{'data': {'cmbd': 'null',
   'id': '18796742',
   'docid': 'null',
   'page': 'null',
   'paragraph': 'null',
   'text': " nº historia clinica: ** *** *** nºepisodi: ******** sexe: dona data de naixement: 06.06.1938 edat: 79 anys procedencia domicil/res.soc servei psiquiatria data d'ingres 10.05.2018 data d'alta 10.05.2018 16:46:41 ates per ****************, ************; *************, assumpta informe d'alta d'hospitalitzacio motiu d'ingres paciente de 79 años que acude derivada a urgencias de psiquiatria tras sim. antecedents -sin alergias mediamentosas conocidas - hipertension arterial en tratamiento farmaoclogico con tres farmacos. - dislipemia en tratamiento farmacologico. - sindrome ansioso depresivo de larga evolucion actualmente en tratamiento con venlafaxina y sertralina. refiere primera vinculacion con red de salud mental en el 2013 a raiz de la muerte desu marido, con sentimientos de tristeza, soledad, rumiaciones respecto a su marido y su muerte e importanteclinica ansios

data -> array. Each cell is one "historia clinica" entry

data[0] -> dictionary with "data" and "anotations" and "predictions"

        -> "data" would be the "x". Contains id, actual text. And other data.

        -> "annotations" seems to be empty
        
        -> "predictions" our "y", "label". Contains the tags for indexes of the text.

data[0]["predictions"][0] <- for some reason nested inside an unnecessary array

data[0]["predictions"][0]["result"] <- also nested inside unnecessary dictionary with one key


data[0]["predictions"][0]["result"] -> inside here we have a list of tags for different ranges.

data[0]["predictions"][0]["result"][0] -> in each of these elements of the list, we have another dictionary

data[0]["pred2ictions"][0]["result"][0]["value"] -> to access a dictionary with the keys "start", "end", and "labels". For start, end index and the tag

data[0]["pred2ictions"][0]["result"][0] -> we have more keys such as "id", "from_name", "to_name" and "type". Use?? differentiate if is label or not? what else can we have?

data[0]["pred2ictions"][0]["result"][0]["value"]["labels"] -> Not sure if we can have more than one tag per range but the tags are in an array in string form ['NEG']

In [2]:
data[2]["predictions"][0]["result"][0]["value"]["labels"]

['NEG']

In [3]:
import torch
from torch.utils.data import Dataset
import numpy as np
import copy

In [4]:
from icecream import ic

In [111]:
class characters_text2tagsDataset(Dataset):
    """
    This class takes the given dataset in form of a list of nested dictionaries
    and outputs a window of sequence_length characters and tags around an id word.
    Given a center word we get from -sequence_lenght/2 to +sequence_lenght/2.
    """

    def __init__(self,data,sequence_length): 
        self.sequence_lenght = sequence_length
        self.data = copy.deepcopy(data)
        self.tags = list(np.empty(len(data)))

        #we'll use this for as we go extract vocab an usable tags
        self.vocab = set()
        self.uniq_tags = set()

        #To start, we should clean up a bit our data, as we noticed that there are a lot of unnecessary empty spaces.
        for i,report in enumerate(data):
            self.remove_empty_spaces(i,report)
        
        #We should padd the reports so that no window of sequence_lenght captures more than one document
        #save previous reports length to later on keep track.
        self.data_l = np.array([len(d["data"]["text"]) for d in data])
        self.dataset_lenght = np.sum(self.data_l) #how many characters over whole reports
        
        for i,report in enumerate(data): #iterate over all reports
            self.extract_vocab(report)
            self.extract_unique_tags(report)
            self.pad_report(i,report)
        
        #get lenghts for padded data
        self.pdata_l = np.array([len(d["data"]["text"]) for d in data])
        self.pdata_cl = np.array([int(np.sum(self.pdata_l[:i])) for i in range(len(self.pdata_l))])
        
        #Manually add a "NONE" tag for untagged characters
        self.uniq_tags.add('NONE')

        #convert vocab and uniq_tags to list so they have an index we can use
        self.vocab = list(self.vocab)
        self.uniq_tags = list(self.uniq_tags)
        #generate tag data for every caracter in each report
        self.generate_tags_data()

    def __len__(self):
       return self.dataset_lenght

    def __getitem__(self, idx): #idx iterates over all characters in the dataset
        assert (idx >= 0) & (idx < self.dataset_lenght), "Dataset index out of range"
        #ic(idx)

        #look at what report of all we are looking at and calculate the index taking into account the paddings:
        # idx passed would be the index of a character among all reports concatenated without padding.
        
        prev_reports = np.where(self.pdata_cl < idx)[0]
        if(len(prev_reports)) == 0: #if all idx are bigger or equal then we are in the first report
            rep_idx = 0 
            real_idx = self.sequence_lenght 
        else:
            rep_idx = prev_reports[-1] #last report is the one we are on
            real_idx = idx - self.pdata_cl[rep_idx] + self.sequence_lenght
        
        #ic(rep_idx)
        #ic(real_idx)

        a_i = real_idx-int(self.sequence_lenght/2)
        b_i = real_idx+int(self.sequence_lenght/2)
        
        #ic(a_i)
        #ic(b_i)

        txt_window = self.data[rep_idx]["data"]["text"][a_i:b_i]
        tag_window = self.tags[rep_idx][a_i:b_i]

        return txt_window, tag_window
    
    ####
    #AUXILIARY FUNCTIONS FOR CLEANER CODE
    ####
    def extract_vocab(self,report):
        for l in list(report["data"]["text"]):
            self.vocab.add(l) #as vocab is a set it will take care of having unique values

    def extract_unique_tags(self,report):
        for tagged_range in report["predictions"][0]["result"]:
            #we checked and this array for all reports only contains one element one label per tagged range
            self.uniq_tags.add(tagged_range["value"]["labels"][0])
    
    def pad_report(self,i,report):
        padd = " "*self.sequence_lenght
        self.data[i]["data"]["text"] = padd + report["data"]["text"] + padd

    def remove_empty_spaces(self,i,report):
        self.data[i]["data"]["text"] = report["data"]["text"].strip()
    
    def generate_tags_data(self):
        for i,report in enumerate(self.data):
            text = report["data"]["text"]
            #start by assigning NONE tag to all characters
            self.tags[i] = np.array(["NONE"]*len(text))
            
            #iterate among know tagged ranges and assign
            for tagged_range in report["predictions"][0]["result"]:
                start_idx = tagged_range["value"]["start"]
                end_idx = tagged_range["value"]["end"]
                tag = tagged_range["value"]["labels"][0]

                #these idx are without taking into account the initial padding so take that into account:
                start_idx += self.sequence_lenght
                end_idx += self.sequence_lenght
                for j in range(start_idx,end_idx): #end_idx +1, the last one is also tagged?  
                    self.tags[i][j] = tag         
    ####
    ####

In [112]:
dataset = characters_text2tagsDataset(data,sequence_length=100)

In [113]:
dataset.__getitem__(1444556)

('    nº historia clinica: ** *** *** nºepisodi: ******** sexe: dona data de naixement: 19.01.1953 eda',
 array(['NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE',

In [114]:
txt, tag = dataset.__getitem__(5304)
len(txt)

100

In [115]:
ic.enable()

In [116]:
dataset.data[1]["data"]["text"][1899:1999]

'                                                                                                   '

In [117]:
dataset.__getitem__(533540)

(' estable, afebril i amb bon control del dolor. bon trofisme distal. donada la bona evolucio clinica ',
 array(['NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NEG', 'NEG', 'NEG', 'NEG', 'NEG', 'NEG', 'NEG',
        'NEG', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE']

In [118]:
dataset.__getitem__(33490)


('erna. debido a la buena evolucion clinica, se decide alta hospitalaria. orientacio diagnostica asma ',
 array(['NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE', 'NONE',
        'NONE', 'NONE', 'NONE',

In [119]:
cnt = 0
cnt2 = 0
for i, (txt, tag) in enumerate(dataset):
    cnt += 1
    if(len(txt) < dataset.sequence_lenght):
        print(i)
        print(len(txt))
        #print(txt)
        #print(tag)
        break
    if(len(np.unique(tag))>1):
        print(i)
        print(txt)
        print(tag)
        cnt2 += 1
    if(cnt2 > 20):
        break

365
 d'ingres paciente de 79 años que acude derivada a urgencias de psiquiatria tras sim. antecedents -s
['NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NEG']
366
d'ingres paciente de 79 años que acude derivada a urgencias de psiquiatria tras sim. antecedents -si
['NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' '

In [86]:
len(dataset)

1611331

In [87]:
cnt

1611331